In [1]:
# disabling contracts for speed
import contracts
import yaml
import numpy as np
import geometry as geo
import numpy as np
from duckietown_world.world_duckietown.tile_template import load_tile_types
from duckietown_world.geo.measurements_utils import iterate_by_class
from duckietown_world.world_duckietown.tile import get_lane_poses
import duckietown_world as dw
from copy import deepcopy
import geometry as g
import pandas as pd

contracts.disable_all()
m = dw.load_map('robotarium2')


INFO:dt-world:duckietown-world 1.0.30
INFO:zj:zj 3.0.3
INFO:zuper-commons:zuper-commons 5.0.7
INFO:dt-world:contracts 1.8.12 


ha


INFO:dt-world:loading map robotarium2


In [2]:
import duckietown_world as dw
from duckietown_world.svg_drawing.ipython_utils import ipython_draw_svg, ipython_draw_html

class Person(dw.PlacedObject):
    def __init__(self, radius, *args, **kwargs):

        self.radius = radius

        dw.PlacedObject.__init__(self, *args, **kwargs)

        

    def draw_svg(self, drawing, g):

        # drawing is done using the library svgwrite

        c = drawing.circle(center=(0, 0), r=self.radius, fill='pink')

        g.add(c)

        # draws x,y axes

        dw.draw_axes(drawing, g)


    def extent_points(self):

        # set of points describing the boundary 

        L = self.radius

        return [(-L, -L), (+L, +L)]

def relative_pose(q0, q1):
    return g.SE2.multiply(g.SE2.inverse(q0), q1)

def interpolate(q0, q1, alpha):
    q1_from_q0 = relative_pose(q0, q1)
    vel = g.SE2.algebra_from_group(q1_from_q0)
    rel = g.SE2.group_from_algebra(vel * alpha)
    q = g.SE2.multiply(q0, rel)
    return q

In [6]:
root = dw.PlacedObject()
import sys
import traceback



realTimestamps = []
seqs2 = []
final_trajectory = []

fileList = ['autobot04_0.yaml', 'autobot04_1.yaml' , 'autobot04_2.yaml' ,'autobot04_3.yaml','autobot04_4.yaml','autobot04_5.yaml'
           ,'autobot04_6.yaml','autobot04_7.yaml','autobot04_8.yaml','autobot04_9.yaml','autobot04_10.yaml',
            'autobot04_11.yaml','autobot04_12.yaml','autobot04_13.yaml','autobot04_14.yaml','autobot04_15.yaml'
           ,'autobot04_16.yaml','autobot04_17.yaml','autobot04_18.yaml','autobot04_19.yaml']

fileLength = 23
for fileName in range(1,24):

    trajectoryFile = 'trajectoryFiles/autobot04/autobot04' + '_' + str(fileName) + '.yaml'
    try:
        print(trajectoryFile)
        with open(trajectoryFile, 'r') as stream:

            try:

                data = yaml.safe_load(stream)

            except yaml.YAMLError as exc:

                print(exc)

    except:
        break

    timestart = data['begin_time_stamp']
    data_points = len(data['trajectory_data'])

    x = np.zeros((data_points,))

    y= np.zeros((data_points,))

    R = np.zeros((3,3, data_points))            
    phi = np.zeros((3, data_points))



    dx = 999.999*np.ones((data_points, ))

    dy = 999.999*np.ones((data_points, ))

    dr = 999.999*np.ones((data_points, ))
    dphi = 999.999*np.ones((data_points, ))


    for idx, [time, traj] in enumerate(data['trajectory_data'].items()):

        x[idx] = np.array(traj[0])

        y[idx] = np.array(traj[1])

        R[:,:,idx] = np.reshape(np.array(traj[3:]), (3,3))


        phi[:,idx] = np.array([np.arctan2(-R[1,2,idx],R[2,2,idx]), 
                               np.arctan2(R[0,2,idx],np.sqrt(R[0,0,idx]**2 + R[0,1,idx]**2)),
                               np.arctan2(-R[0,1,idx], R[0,0,idx])])

        realTimestamps.append(time)
        #print(phi[:,idx])
        z = phi[2,idx]
        points = np.array([x[idx], y[idx]])
        final_trajectory.append([points, z])
        
final_array = final_trajectory

print(len(final_array))

for entry in range(0, len(final_array)):
    x =  (final_array[entry][0][0] )  # -2.2
    y = final_array[entry][0][1] # + 0.8
    alpha = final_array[entry][1]
    q5 = geo.SE2_from_translation_angle([x,y],alpha)
    seqs2.append(q5)



trajectoryFiles/autobot04/autobot04_1.yaml
trajectoryFiles/autobot04/autobot04_2.yaml
trajectoryFiles/autobot04/autobot04_3.yaml
trajectoryFiles/autobot04/autobot04_4.yaml
trajectoryFiles/autobot04/autobot04_5.yaml
trajectoryFiles/autobot04/autobot04_6.yaml
trajectoryFiles/autobot04/autobot04_7.yaml
trajectoryFiles/autobot04/autobot04_8.yaml
trajectoryFiles/autobot04/autobot04_9.yaml
trajectoryFiles/autobot04/autobot04_10.yaml
trajectoryFiles/autobot04/autobot04_11.yaml
trajectoryFiles/autobot04/autobot04_12.yaml
trajectoryFiles/autobot04/autobot04_13.yaml
trajectoryFiles/autobot04/autobot04_14.yaml
trajectoryFiles/autobot04/autobot04_15.yaml
trajectoryFiles/autobot04/autobot04_16.yaml
trajectoryFiles/autobot04/autobot04_17.yaml
trajectoryFiles/autobot04/autobot04_18.yaml
trajectoryFiles/autobot04/autobot04_19.yaml
trajectoryFiles/autobot04/autobot04_20.yaml
2727


In [ ]:

timestamps = range(len(seqs2)) # [0, 1, 2, ...]
# SE2Transform is the wrapper for SE2 used by Duckietown World 
transforms = [dw.SE2Transform.from_SE2(_) for _ in seqs2]
seq_me = dw.SampledSequence(timestamps, transforms)
counter = 0
center_points2 = []
width = 0

for timestamp, pose_object in seq_me:
    print(counter)
    hoi = list(get_lane_poses(m, pose_object.as_SE2()))
    
    if len(hoi) == 0:
        # Now has only zero length when in asphalt
        print(' ')
        #print(dw.SE2Transform.from_SE2(geo.SE2_from_translation_angle([0,0],0)))
        #center_points2.append(dw.SE2Transform.from_SE2(geo.SE2_from_translation_angle([0,0],0)))
        
    else:
        #print('outside left: ' + str(hoi[0].lane_pose.distance_from_left) + ' outside right: ' + str(hoi[0].lane_pose.distance_from_right))
        distance_from_left = hoi[0].lane_pose.distance_from_left
        distance_from_right = hoi[0].lane_pose.distance_from_right
        distance_from_center = hoi[0].lane_pose.distance_from_center
        rel_heading = hoi[0].lane_pose.relative_heading
        alongInside = hoi[0].lane_pose.along_inside
        outsideLeft = hoi[0].lane_pose.outside_left
        inside = hoi[0].lane_pose.inside
        lateral = hoi[0].lane_pose.lateral
        lateral_left = hoi[0].lane_pose.lateral_left
        width = lateral_left
        tile = list(hoi[0].tile.children.keys())[0]

        correctDir = hoi[0].lane_pose.correct_direction
        print(timestamp, distance_from_center, tile)
        #print(timestamp, distance_from_center, rel_heading) 
        
        #absTime = float(relTimestamps[counter]) + int(timestart)
        center_points2.append(hoi[0].lane_pose.center_point)
        #print(hoi[0].lane_pose.distance_from_center, hoi[0].lane_pose.relative_heading)
    #lane_pose = lanesegment.lane_pose_from_SE2Transform(pose_object)    
    #center_points.append(lane_pose.center_point)
    #print(relTimestamps[counter])

    counter += 1
    print(' ')


0
('tilemap', 'tile-0-3', '3way_left', 'west_go_straight')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.48752137529849937,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.2923076547384258,relative_heading=-1.4997766998548994,distance_from_left=0.29952137529849937,distance_from_right=0.6755213752984994,distance_from_center=0.48752137529849937,center_point=SE2Transform([-0.2076923452615742, -0.2199999988079071],0.0),correct_direction=True)
('tilemap', 'tile-0-3', '3way_left', 'west_go_left')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.33540103877800836,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.6403868452536857,relative_heading=-2.397025012897812,distance_from_left=0.14740103877800836,distance_from_right=0.5234010387780084,distance_from_center=0.33540103877800836,center_poin

('tilemap', 'tile-0-3', '3way_left', 'north_go_right')
LanePose(inside=True,lateral_inside=True,outside_left=False,outside_right=False,lateral=0.088640999618397,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.18878204273354107,relative_heading=0.6823467846253299,distance_from_left=0.099359000381603,distance_from_right=0.276640999618397,distance_from_center=0.088640999618397,center_point=SE2Transform([-0.32432882948051206, -0.27883827504797726],-0.6707664916477449),correct_direction=True)
('tilemap', 'tile-0-3', '3way_left', 'east_go_right')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.46486289384386714,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.3536759667223184,relative_heading=2.8390320718344046,distance_from_left=0.27686289384386714,distance_from_right=0.6528628938438672,distance_from_center=0.46486289384386714,cent

6.0 0.4892307770252221 3way_left
 
7
('tilemap', 'tile-0-3', '3way_left', 'west_go_straight')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.4892307770252221,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.2905982530117033,relative_heading=-1.5659463163230571,distance_from_left=0.3012307770252221,distance_from_right=0.6772307770252222,distance_from_center=0.4892307770252221,center_point=SE2Transform([-0.20940174698829672, -0.2199999988079071],0.0),correct_direction=True)
('tilemap', 'tile-0-3', '3way_left', 'west_go_left')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.3378144684347694,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.6408992433446493,relative_heading=-2.463912552192352,distance_from_left=0.14981446843476942,distance_from_right=0.5258144684347694,distance_from_center

('tilemap', 'tile-0-3', '3way_left', 'east_go_right')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.46486289384386714,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.3536759667223184,relative_heading=2.8320817920724335,distance_from_left=0.27686289384386714,distance_from_right=0.6528628938438672,distance_from_center=0.46486289384386714,center_point=SE2Transform([-0.23271182826010434, -0.41287300360676005],-1.256655452061923),correct_direction=False)
('tilemap', 'tile-0-3', '3way_left', 'east_go_straight')
LanePose(inside=True,lateral_inside=True,outside_left=False,outside_right=False,lateral=-0.04923077702522213,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.7094017469882967,relative_heading=1.5754263400105106,distance_from_left=0.23723077702522213,distance_from_right=0.13876922297477787,distance_from_center=-0.04923077702

('tilemap', 'tile-0-3', '3way_left', 'north_go_right')
LanePose(inside=True,lateral_inside=True,outside_left=False,outside_right=False,lateral=0.10641704314510142,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.1787546078082892,relative_heading=0.643097816882271,distance_from_left=0.08158295685489858,distance_from_right=0.2944170431451014,distance_from_center=0.10641704314510142,center_point=SE2Transform([-0.33236681677065955, -0.27284414709310584],-0.6351377462032916),correct_direction=True)
('tilemap', 'tile-0-3', '3way_left', 'east_go_right')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.44372819375006917,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.3510109015556662,relative_heading=2.825942535686012,distance_from_left=0.25572819375006917,distance_from_right=0.6317281937500692,distance_from_center=0.44372819375006917,

...

('tilemap', 'tile-4-3', '3way_left', 'north_go_left')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.3165840823018413,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.16191837103833925,relative_heading=-2.7052107374520418,distance_from_left=0.12858408230184132,distance_from_right=0.5045840823018413,distance_from_center=0.3165840823018413,center_point=SE2Transform([-0.3399039436037278, -0.19821563676557338],0.22686441778186836),correct_direction=False)
('tilemap', 'tile-4-3', '3way_left', 'north_go_right')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.33618769595906295,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.040631114190338914,relative_heading=-2.3339788283423006,distance_from_left=0.14818769595906295,distance_from_right=0.524187695959063,distance_from_center=0.3361876959590

('tilemap', 'tile-3-3', 'straight', 'lane1')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.20034184467792418,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.10256406307220534,relative_heading=0.08935888796645644,distance_from_left=0.01234184467792418,distance_from_right=0.3883418446779242,distance_from_center=0.20034184467792418,center_point=SE2Transform([-0.39743593692779466, -0.2199999988079071],0.0),correct_direction=True)
('tilemap', 'tile-3-3', 'straight', 'lane2')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.23965815532207588,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.8974359369277947,relative_heading=-3.0522337656233365,distance_from_left=0.05165815532207588,distance_from_right=0.42765815532207585,distance_from_center=0.23965815532207588,center_point=SE2Transform([0.

('tilemap', 'tile-3-3', 'straight', 'lane1')
LanePose(inside=True,lateral_inside=True,outside_left=False,outside_right=False,lateral=0.1319657756090156,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.4632478274106986,relative_heading=-0.3224589039499244,distance_from_left=0.056034224390984405,distance_from_right=0.3199657756090156,distance_from_center=0.1319657756090156,center_point=SE2Transform([-0.03675217258930141, -0.2199999988079071],0.0),correct_direction=True)
('tilemap', 'tile-3-3', 'straight', 'lane2')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.3080342243909844,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.5367521725893014,relative_heading=2.819133749639869,distance_from_left=0.12003422439098438,distance_from_right=0.4960342243909844,distance_from_center=0.3080342243909844,center_point=SE2Transform([0.03675217

('tilemap', 'tile-3-3', 'straight', 'lane2')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.44991456770896954,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.11794874954223594,relative_heading=2.7846197341914856,distance_from_left=0.26191456770896954,distance_from_right=0.6379145677089695,distance_from_center=0.44991456770896954,center_point=SE2Transform([-0.38205125045776406, -0.2199999988079071],0.0),correct_direction=False)
2524.0 -0.009914567708969563 straight
 
2525
('tilemap', 'tile-3-3', 'straight', 'lane1')
LanePose(inside=True,lateral_inside=True,outside_left=False,outside_right=False,lateral=-0.02700858497619693,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.9264956953525547,relative_heading=-0.3670560889489214,distance_from_left=0.21500858497619693,distance_from_right=0.16099141502380307,distance_from_center=-0.0

('tilemap', 'tile-2-3', '3way_left', 'west_go_left')
LanePose(inside=False,lateral_inside=False,outside_left=False,outside_right=True,lateral=-0.2171426452119054,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.981032673096994,relative_heading=1.408040754607592,distance_from_left=0.4051426452119054,distance_from_right=0.029142645211905405,distance_from_center=-0.2171426452119054,center_point=SE2Transform([0.20326559256800902, 0.36114855396440204],1.3745284197282508),correct_direction=True)
('tilemap', 'tile-2-3', '3way_left', 'north_go_left')
LanePose(inside=False,lateral_inside=False,outside_left=True,outside_right=False,lateral=0.5131523040308263,lateral_left=0.188,lateral_right=-0.188,along_inside=True,along_before=False,along_after=False,along_lane=0.807548343208191,relative_heading=-3.0612787010399587,distance_from_left=0.32515230403082634,distance_from_right=0.7011523040308263,distance_from_center=0.5131523040308263,cente

In [ ]:
#sequence = dw.SampledSequence(seq_me.timestamps, seq_me.center_points)
#m.set_object("projection2", dw.PlacedObject(), ground_truth=seq_me)
m = dw.load_map('robotarium2')

m.set_object("emded", Person(0.1), ground_truth=seq_me)
ipython_draw_html(m);
